<a href="https://www.kaggle.com/code/mikedelong/friends-topics-with-bertopic?scriptVersionId=147985220" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
%env TOKENIZERS_PARALLELISM=false
!pip install bertopic

env: TOKENIZERS_PARALLELISM=false
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.4/143.4 kB 5.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 52.6 MB/s eta 0:00:00
  Installing build dependencies ... - \ | / - \ | / done
  Getting requirements to build wheel ... - done
  Preparing metadata (pyproject.toml) ... - done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 6.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... - done
  Created wheel for hdbscan: filename=hdbscan-0.8.33-cp310-cp310-linux_x86_64.whl size=819467 sha256=8105f13be89e89958ad516602324595983e2e85f2c48d3d3a6c4c4be18001aa9
  Stored in directory: /root/.cache/pip/wheels/75/0b/3b/dc4f60b7cc455efaefb62883a7483e76f09d06ca81cf87d610
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125926 sha256=68e3e757fb594372ef55e6d789b35ec6a923f52618867b17e4c2d155c02c1145
  Stored in directory: /root/.cache/pip/wheels/62/f2

In [2]:
import pandas as pd
# we are doing word stuff so we don't really need any of the numerical columns
usecols=['text', 'speaker', 'season', 'episode', 'scene', 'utterance'][:2]
df = pd.read_csv(filepath_or_buffer='/kaggle/input/friends/friends.csv', usecols=usecols)
# we are going to throw away very short documents
df['token count'] = df['text'].apply(lambda x: len(x.split()))
df = df[df['token count'] > 2].drop(columns=['token count'])
df.head()

text           speaker
0  There's nothing to tell! He's just some guy I ...     Monica Geller
1  C'mon, you're going out with the guy! There's ...    Joey Tribbiani
2  All right Joey, be nice. So does he have a hum...     Chandler Bing
3                           Wait, does he eat chalk?     Phoebe Buffay
4                         (They all stare, bemused.)  Scene Directions

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 54751 entries, 0 to 67371
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   text     54751 non-null  object
 1   speaker  54672 non-null  object
dtypes: object(2)
memory usage: 1.3+ MB


In [4]:
# let's build our stopword collection
# we collected these from the wordcloud package in a previous run
wordcloud_stopwords = ['a', 'about', 'above', 'after', 'again', 'against', 'all', 'also', 'am', 'an', 'and', 'any', 'are', "aren't", 'as', 'at', 'be', 'because', 'been', 'before', 'being', 'below', 'between', 'both', 'but', 'by', 'can', "can't", 'cannot', 'com', 'could', "couldn't", 'did', "didn't", 'do', 'does', "doesn't", 'doing', "don't", 'down', 'during', 'each', 'else', 'ever', 'few', 'for', 'from', 'further', 'get', 'had', "hadn't", 'has', "hasn't", 'have', "haven't", 'having', 'he', "he'd", "he'll", "he's", 'hence', 'her', 'here', "here's", 'hers', 'herself', 'him', 'himself', 'his', 'how', "how's", 'however', 'http', 'i', "i'd", "i'll", "i'm", "i've", 'if', 'in', 'into', 'is', "isn't", 'it', "it's", 'its', 'itself', 'just', 'k', "let's", 'like', 'me', 'more', 'most', "mustn't", 'my', 'myself', 'no', 'nor', 'not', 'of', 'off', 'on', 'once', 'only', 'or', 'other', 'otherwise', 'ought', 'our', 'ours', 'ourselves', 'out', 'over', 'own', 'r', 'same', 'shall', "shan't", 'she', "she'd", "she'll", "she's", 'should', "shouldn't", 'since', 'so', 'some', 'such', 'than', 'that', "that's", 'the', 'their', 'theirs', 'them', 'themselves', 'then', 'there', "there's", 'therefore', 'these', 'they', "they'd", "they'll", "they're", "they've", 'this', 'those', 'through', 'to', 'too', 'under', 'until', 'up', 'very', 'was', "wasn't", 'we', "we'd", "we'll", "we're", "we've", 'were', "weren't", 'what', "what's", 'when', "when's", 'where', "where's", 'which', 'while', 'who', "who's", 'whom', 'why', "why's", 'with', "won't", 'would', "wouldn't", 'www', 'you', "you'd", "you'll", "you're", "you've", 'your', 'yours', 'yourself', 'yourselves']
# let's add in some stopwords from looking at topic -1 in prior runs
prior_stopwords = ['Oh', 'Im', 'dont', 'know', 'No', 'What', 'great', 'believe', 'Well', 'thing', 'um', 'feel', 'way', 'uh', 'youre', 'You', 'Youre',
                  'thats', 'theres', 'right', 'think', 'Yeah', 'We', 'said', 'Ooh', 'things', 'little', 'gonna', 'want',
                   'And', 'one', 'got', 'The', 'really', 'So', 'All', 'Its', 'go', 'see', 'Okay', 'Thats', 'need',  'guys', 'Go',  'back', 'Ill', 'wanna', 'mean', 'cant', 'play', 'Hey', 'going',
                   'getting', 'Scene', 'look', 'now', 'tell', 'good', 'us', 'take', 'time', 'well', 'something', 'Hi', 'Look', 'didnt',
                   'Do', 'lot', 'better', 'new', 'guy', 'much', 'big', 'This', 'give', 'maybe', 'But', 'That', 'make', 'Yknow', 'sorry', 'say', 'Just', 'help',
                   'Ive', 'talking', 'will', 'II', 'come', 'Wow', 'never', 'yknow', 'okay', 'wait', 'night', 'nothing', 'together', 'actually', 'hundred', 'yeah', 'man', 'enough',
                  'uhoh', 'Uhoh', 'OK', 'iswhat', 'Are', 'knowJust', 'Hes', 'hes', 'He', ]
stopwords = wordcloud_stopwords + prior_stopwords
stopwords = stopwords + [word.capitalize() for word in stopwords] + [word.lower() for word in stopwords]
stopwords = sorted(list(set(stopwords)))
print(stopwords[:20])

['A', 'About', 'Above', 'Actually', 'After', 'Again', 'Against', 'All', 'Also', 'Am', 'An', 'And', 'Any', 'Are', "Aren't", 'As', 'At', 'Back', 'Be', 'Because']


In [5]:
from arrow import now
from bertopic import BERTopic
from plotly.express import histogram
from sklearn.feature_extraction.text import CountVectorizer

MAX_DF = 0.3 # this is a guess and we should probably base it on something
MIN_DF = 3 # our documents are short and there is probably no point in keeping any word that appears twice or less
# we can dial this up and down for testing; a full run (1.0) takes nearly seven minutes
SAMPLE_FRACTION = 1.0

time_start = now()
large_model = BERTopic(verbose=True, top_n_words=15, nr_topics=None, language='english', 
                       vectorizer_model=CountVectorizer(stop_words=stopwords, lowercase=False, min_df=MIN_DF, max_df=MAX_DF, ))
large_topics, large_probs = large_model.fit_transform(df['text'].sample(frac=SAMPLE_FRACTION, random_state=2023).dropna().values)
print('After {} our model says we have {} topics.'.format(now() - time_start, len(set(large_topics))))
print('And we have {} documents with no topic ({}%).'.format(large_topics.count(-1), round(100 * large_topics.count(-1)/len(large_topics))))
histogram(x=[item for item in large_topics if item > -1], title = 'topic > -1 histogram')

/opt/conda/lib/python3.10/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/opt/conda/lib/python3.10/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/opt/conda/lib/python3.10/site-packages/umap/distances.py:1086: NumbaDeprecationWarning: The 'nopython' keyword argume

Batches:   0%|          | 0/1711 [00:00<?, ?it/s]

2023-10-25 16:14:42,104 - BERTopic - Transformed documents to Embeddings
2023-10-25 16:16:19,898 - BERTopic - Reduced dimensionality
2023-10-25 16:16:26,120 - BERTopic - Clustered reduced embeddings


After 0:08:25.648836 our model says we have 790 topics.
And we have 18174 documents with no topic (33%).


In [6]:
large_model.visualize_topics(width=1000, height=1000)

In [7]:
from math import sqrt
from plotly.express import scatter
from sklearn.manifold import TSNE
from plotly.express.colors import sequential


HEIGHT = 800

def visualize(model, term):
    # let's build a DataFrame of the first 20 topics that include our term
    # and their top terms, along with their weights
    word = []
    topic_indices = []
    topic_probability = []
    word_indices = []
    word_weight = []
    overall_weight = []
    topics, probabilities = model.find_topics(search_term=term, top_n=10)
    for topic_index, topic in enumerate(topics):
        probability = probabilities[topic_index]
        topic_result = model.get_topic(topic=topic)
        for word_index, word_result in enumerate(topic_result):
            word.append(word_result[0])
            topic_indices.append(topic_index)
            topic_probability.append(probability)
            word_indices.append(word_index)
            word_weight.append(word_result[1])
            # let's use the geometric mean to get individual word weights within our sample
            overall_weight.append(sqrt(probability * word_result[1]))
    plot_df = pd.DataFrame(data={'word': word, 'topic_index': topic_indices, 
                                 'topic_probability': topic_probability, 'word_index': word_indices,
                                 'word_weight': word_weight,'overall_weight': overall_weight})
    # terms can recur, so let's get the 'heaviest' occurrence using the overall weight
    plot_df = plot_df.sort_values(ascending=False, by='overall_weight').drop_duplicates(keep='first', subset=['word'])
    # now we want to transform the data we have into something that looks nice in a graph but also
    # keeps the relationships we have from the weight and rank data above
    tsne = TSNE(n_components=2, learning_rate='auto', n_iter=1000, init='random', random_state=2023, verbose=0)
    plot_df[['x', 'y']] = tsne.fit_transform(X=plot_df.drop(columns=['word']))
    # we use the overall weight for both the color and the size to differentiate the more
    # important words from the others
    scatter(data_frame=plot_df,
            x='x', y='y', text='word', color='overall_weight', size='overall_weight',
            color_continuous_scale=sequential.Jet, title=term, height=HEIGHT,
            # our colorbar doesn't mean anything intuitive so let's remove it
           ).update_traces(textposition='middle right').update_coloraxes(showscale=False).show()

visualize(model=large_model, term='Perk')

In [8]:
for term in ['Phoebe', 'Rachel', 'Chandler', 'relationship', 'breakup', 'Marcel', 'U2', 'leather', 'armadillo']:
    visualize(model=large_model, term=term)